In [5]:
import pandas as pd
from urllib.parse import urlparse, urlunparse, parse_qsl, urlencode

def filterLog(filename):
    # Specify the file path
    file_path = f'{filename}.csv'

    # Read the CSV file without headers
    df = pd.read_csv(file_path)

    # Select the relevant column
    selected_columns = df[['request_headers', 'request_body', 'url', 'method']]

    
    selected_columns = selected_columns.rename(columns={
    'request_headers': 'Request.Headers',
    'request_body': 'Request.Body',
    'url': 'Request.URL',
    'method': 'Request.Method'
})

    # # Function to extract path and query params from a URL
    # def extract_path_and_query(url):
    #     parsed_url = urlparse(url)
    #     # Extract path and query parameters
    #     path = parsed_url.path
    #     query_params = urlencode(dict(parse_qsl(parsed_url.query)))
    #     # Combine the path and the formatted query parameters
    #     if query_params:
    #         return f'{path}?{query_params}'
    #     return path
    # # Apply the function to the 'endpoint' column
    # selected_columns['endpoint'] = selected_columns['endpoint'].apply(extract_path_and_query)
    
    print(len(selected_columns))
    # Specify the path for the new CSV file
    output_file_path = 'http_health.csv'
    
    # Save the filtered dataframe to a new CSV file with only the filtered 'endpoint'
    selected_columns.to_csv(output_file_path, index=False)



In [6]:
filterLog("./../healthioProxy")

20641


In [7]:
import csv
import requests

# Path to your CSV file
csv_file_path = 'http_health.csv'

# Base URL for localhost
base_url = 'http://localhost:8080'
# Function to parse headers from the string format
def parse_headers(headers_str):
    headers = {}
    if headers_str.strip():  # Ensure headers string is not empty
        header_lines = headers_str.splitlines()
        for line in header_lines:
            # Split by the first occurrence of ':' to handle values that may also contain ':'
            if ':' in line:
                key, value = line.split(':', 1)
                headers[key.strip()] = value.strip()
    return headers

# Function to send the HTTP request
def send_http_request(method, endpoint, headers, body):
    url = base_url + endpoint
    headers = parse_headers(headers)
    try:
        if method == 'POST':
            response = requests.post(url, headers=headers, data=body)
        elif method == 'GET':
            response = requests.get(url, headers=headers)
        elif method == 'PUT':
            response = requests.put(url, headers=headers, data=body)
        elif method == 'DELETE':
            response = requests.delete(url, headers=headers)
        elif method == 'PATCH':
            response = requests.patch(url, headers=headers, data=body)
        elif method == 'HEAD':
            response = requests.head(url, headers=headers)
        elif method == 'OPTIONS':
            response = requests.options(url, headers=headers)
        else:
            print(f"HTTP method {method} not supported.")
            return None
        return response
    except requests.RequestException as e:
        print(f"Error sending {method} request to {url}: {e}")
        return None

# Open the CSV file and process each row
with open(csv_file_path, mode='r', newline='', encoding='utf-8') as file:
    csv_reader = csv.DictReader(file)
    
    for row in csv_reader:
        request_headers = row['request_header']
        request_body = row['request_body']
        request_endpoint = row['endpoint']
        request_method = row['method']
        
        print(f"Sending {request_method} request to {base_url}{request_endpoint}...")
        response = send_http_request(request_method, request_endpoint, request_headers, request_body)
        
        if response:
            print(f"Response Status Code: {response.status_code}")
            print(f"Response Body: {response.text}")
        


FileNotFoundError: [Errno 2] No such file or directory: 'http_requests.csv'

In [4]:
import requests
import pandas as pd
import json

# Load the CSV file
file_path = 'http_requests_recapped.csv'
requests_df = pd.read_csv(file_path)

# Loop through each row in the dataframe and send requests to the firewall
for index, row in requests_df.iterrows():
    url = row['Request.URL'].replace('https://', 'http://localhost:8080/')
    headers = dict(line.split(': ', 1) for line in row['Request.Headers'].split('\r\n') if line)
    method = row['Request.Method']
    body = row['Request.Body'] if pd.notna(row['Request.Body']) else None

    try:
        if method == 'POST':
            # Check if it's a GraphQL request based on URL or headers (or any other condition)
            if "graphql" in url.lower() or "graphql" in headers.get('Content-Type', '').lower():
                # Convert body to JSON if it's not already
                graphql_query = json.loads(body) if body else {"query": "", "variables": {}}
                response = requests.post(url, headers=headers, json=graphql_query)
            else:
                # Regular POST request
                response = requests.post(url, headers=headers, data=body)

        elif method == 'GET':
            response = requests.get(url, headers=headers)
        elif method == 'PUT':
            response = requests.put(url, headers=headers, data=body)
        elif method == 'DELETE':
            response = requests.delete(url, headers=headers)
        elif method == 'PATCH':
            response = requests.patch(url, headers=headers, data=body)
        elif method == 'HEAD':
            response = requests.head(url, headers=headers)
        elif method == 'OPTIONS':
            # GraphQL-specific OPTIONS request
            if "graphql" in url.lower() or "graphql" in headers.get('Content-Type', '').lower():
                # GraphQL OPTIONS requests don't need body data
                response = requests.options(url, headers=headers)
            else:
                # Regular OPTIONS request
                response = requests.options(url, headers=headers)
        else:
            print(f"HTTP method {method} not supported.")

        # Print response status code and details
        print(f"Request {index + 1}: Status Code: {response.status_code}")
        print(f"Response: {response.text[:200]}...")  # Limiting output for readability
    except Exception as e:
        print(f"Request {index + 1}: Failed with error: {str(e)}")


Request 1: Failed with error: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
Request 2: Failed with error: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
Request 3: Failed with error: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
Request 4: Status Code: 403
Response: <html>
<head><title>403 Forbidden</title></head>
<body>
<center><h1>403 Forbidden</h1></center>
<hr><center>nginx</center>
</body>
</html>
...
Request 5: Failed with error: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
Request 6: Status Code: 403
Response: <html>
<head><title>403 Forbidden</title></head>
<body>
<center><h1>403 Forbidden</h1></center>
<hr><center>nginx</center>
</body>
</html>
...
Request 7: Status Code: 403
Response: <html>
<head><title>403 Forbidden</title></head>
<body>
<center><h1>403 Forbidden</h1></center>
<hr><center>

In [6]:
import requests
import pandas as pd
from concurrent.futures import ThreadPoolExecutor, as_completed

# Load the CSV file
file_path = 'http_requests_recapped.csv'
requests_df = pd.read_csv(file_path)

# Function to send requests
def send_request(index, row):
    url = row['Request.URL'].replace('https://', 'http://localhost:8080/')
    headers = dict(line.split(':', 1) for line in row['Request.Headers'].split('\r\n') if line)
    method = row['Request.Method']
    body = row['Request.Body'] if pd.notna(row['Request.Body']) else None

    try:
        if method == 'POST':
            response = requests.post(url, headers=headers, data=body)
        elif method == 'GET':
            response = requests.get(url, headers=headers)
        elif method == 'PUT':
            response = requests.put(url, headers=headers, data=body)
        elif method == 'DELETE':
            response = requests.delete(url, headers=headers)
        elif method == 'PATCH':
            response = requests.patch(url, headers=headers, data=body)
        elif method == 'HEAD':
            response = requests.head(url, headers=headers)
        elif method == 'OPTIONS':
            response = requests.options(url, headers=headers)
        else:
            return (index, f"HTTP method {method} not supported.")
        
        # Returning status and part of the response
        return (index, f"Status Code: {response.status_code}", f"Response: {response.text[:200]}...")
    except Exception as e:
        return (index, f"Failed with error: {str(e)}")

# Using ThreadPoolExecutor for multithreading
with ThreadPoolExecutor(max_workers=10) as executor:
    # Submit all requests to be executed concurrently
    future_to_index = {executor.submit(send_request, index, row): index for index, row in requests_df.iterrows()}

    # Process the results as they complete
    for future in as_completed(future_to_index):
        index = future_to_index[future]
        try:
            result = future.result()
            print(f"Request {result[0] + 1}: {result[1]}")
            if len(result) > 2:
                print(result[2])
        except Exception as e:
            print(f"Request {index + 1}: Failed with exception {e}")


Request 29: Failed with error: Invalid leading whitespace, reserved character(s), or return character(s) in header value: ' js.hs-banner.com\nUser-Agent: Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:129.0) Gecko/20100101 Firefox/129.0\nAccept: */*\nAccept-Language: en-US,en;q=0.5\nAccept-Encoding: gzip, deflate, br\nSec-Fetch-Dest: script\nSec-Fetch-Mode: no-cors\nSec-Fetch-Site: cross-site\nTe: trailers\nConnection: keep-alive'
Request 22: Failed with error: Invalid leading whitespace, reserved character(s), or return character(s) in header value: ' scout.salesloft.com\nUser-Agent: Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:129.0) Gecko/20100101 Firefox/129.0\nAccept: */*\nAccept-Language: en-US,en;q=0.5\nAccept-Encoding: gzip, deflate, br\nOrigin: https://staging.recapped.io\nSec-Fetch-Dest: empty\nSec-Fetch-Mode: cors\nSec-Fetch-Site: cross-site\nTe: trailers'
Request 42: Failed with error: Invalid leading whitespace, reserved character(s), or return character(s) in header

In [10]:
import csv
import requests
from concurrent.futures import ThreadPoolExecutor, as_completed

# Path to your CSV file
csv_file_path = 'http_requests_xss.csv'

# Base URL for localhost
base_url = 'http://localhost:8080'

# Function to parse headers from the string format
def parse_headers(headers_str):
    headers = {}
    if headers_str.strip():  # Ensure headers string is not empty
        header_lines = headers_str.splitlines()
        for line in header_lines:
            # Split by the first occurrence of ':' to handle values that may also contain ':'
            if ':' in line:
                key, value = line.split(':', 1)
                headers[key.strip()] = value.strip()
    return headers

# Function to send the HTTP request
def send_http_request(method, endpoint, headers, body):
    url = endpoint.replace('https://', 'http://localhost:8080/')
    headers = parse_headers(headers)
    print("headersss: ",headers)
    try:
        if method == 'POST':
            response = requests.post(url, headers=headers, data=body)
        elif method == 'GET':
            response = requests.get(url, headers=headers)
        elif method == 'PUT':
            response = requests.put(url, headers=headers, data=body)
        elif method == 'DELETE':
            response = requests.delete(url, headers=headers)
        elif method == 'PATCH':
            response = requests.patch(url, headers=headers, data=body)
        elif method == 'HEAD':
            response = requests.head(url, headers=headers)
        elif method == 'OPTIONS':
            response = requests.options(url, headers=headers)
        else:
            print(f"HTTP method {method} not supported.")
            return None
        return response
    except requests.RequestException as e:
        print(f"Error sending {method} request to {url}: {e}")
        return None

def process_request(row):
    request_headers = row['Request.Headers']
    request_body = row['Request.Body']
    request_endpoint = row['Request.URL']
    request_method = row['Request.Method']
    
    # print(f"Sending {request_method} request to {base_url}{request_endpoint}...")
    response = send_http_request(request_method, request_endpoint, request_headers, request_body)
    
    if response:
        return {
            'endpoint': request_endpoint,
            'method': request_method,
            'status_code': response.status_code,
            'response_body': response.text
        }
    else:
        return None

# Open the CSV file and process each row using multithreading
def send():
    with open(csv_file_path, mode='r', newline='', encoding='utf-8') as file:
        csv_reader = csv.DictReader(file)
        requests_data = [row for row in csv_reader]  # Load all rows

    with ThreadPoolExecutor(max_workers=15) as executor:
        # Submit tasks to be executed concurrently
        futures = [executor.submit(process_request, row) for row in requests_data]

        # Process the results as they complete
        for future in as_completed(futures):
            result = future.result()
            if result:
                print(f"Response for {result['method']} to {result['endpoint']}:")
                print(f"Status Code: {result['status_code']}")
                print(f"Response Body: {result['response_body']}\n")




In [11]:
send()

headersss: headersss:  {'Host': 'example.com', 'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:130.0) Gecko/20100101 Firefox/130.0', 'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/png,image/svg+xml,*/*;q=0.8', 'Accept-Language': 'en-US,en;q=0.5', 'Accept-Encoding': 'gzip, deflate, br', 'Dnt': '1', 'Sec-Gpc': '1', 'Upgrade-Insecure-Requests': '1', 'Sec-Fetch-Dest': 'document', 'Sec-Fetch-Mode': 'navigate', 'Sec-Fetch-Site': 'cross-site', 'If-Modified-Since': 'Thu, 17 Oct 2019 07:18:26 GMT', 'If-None-Match': '"3147526947"', 'Priority': 'u=0, i', 'Te': 'trailers', 'Connection': 'keep-alive'}
 {'Host': 'example.com', 'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:130.0) Gecko/20100101 Firefox/130.0', 'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/png,image/svg+xml,*/*;q=0.8', 'Accept-Language': 'en-US,en;q=0.5', 'Accept-Encoding': 'gzip, deflate, br', 'Dnt': '1', 'Se

In [10]:
import re
import json


def extract_transactions(log_file):
    transactions = []
    with open(log_file, 'r') as file:
        log_data = file.read()

    # Regular expression to find the start of the transaction object
    transaction_start_pattern = r'(\{"transaction":\{)'
    matches = re.finditer(transaction_start_pattern, log_data)

    for match in matches:
        start_index = match.start()
        
        # Use a stack to handle nested curly braces and find the end of the transaction object
        brace_stack = []
        for i in range(start_index, len(log_data)):
            char = log_data[i]
            if char == '{':
                brace_stack.append('{')
            elif char == '}':
                brace_stack.pop()
                if not brace_stack:
                    # If the stack is empty, we've found the end of the transaction object
                    end_index = i + 1
                    transactions.append(log_data[start_index:end_index])
                    break

    return transactions
def filter_xss_transactions(transactions):
    xss_transactions = []
    for transaction in transactions:
        try:
            # Convert the transaction string to a Python dictionary
            transaction_data = json.loads(transaction)
            # Check if 'tags' contain 'attack-xss'
            if "messages" in transaction_data["transaction"]:
                for message in transaction_data["transaction"]["messages"]:
                    if "tags" in message["details"] and "attack-xss" in message["details"]["tags"]:
                        xss_transactions.append(transaction)
                        break
        except json.JSONDecodeError as e:
            print(f"Error decoding JSON: {e}")
            continue
    
    return xss_transactions

def save_transactions(transactions, output_file):
    with open(output_file, 'w') as file:
        for transaction in transactions:
            file.write(transaction + '\n')

In [11]:
log_file = 'logs/all.log'  # Replace with your actual log file name
output_file = 'logs/gwrrr.json'

# Extract transactions
transactions = extract_transactions(log_file)

# Save the extracted transactions to a JSON file
save_transactions(transactions, output_file)

print(f"Extracted {len(transactions)} transactions and saved to {output_file}")

Extracted 4442 transactions and saved to logs/gwrrr.json


In [28]:
import re

# Define the regular expression pattern for "application-attack-xss" (case insensitive)
pattern = re.compile(r'APPLICATION-ATTACK-RCE', re.IGNORECASE)

# Open the input log file and the new log file for writing
with open('logs/host-fs-auditlog.log', 'r', encoding='utf-8', errors='ignore') as infile, open('logs/rce_attack_log_blackboard.log', 'w', encoding='utf-8') as outfile:
    # Iterate over each line in the input file
    for line in infile:
        # If the pattern is found in the line, write it to the output file
        if pattern.search(line):
            outfile.write(line)

print("Filtered log file created successfully!")


Filtered log file created successfully!
